In [13]:
import json
import numpy as np
import pandas as pd
import plotly.express as px
import mlxtend as mlx
from tqdm.notebook import tqdm, trange
from itertools import chain

In [14]:
def read_json(path):
    file = open(path,'r+', encoding='utf-8')
    data = {}
    for line in file.readlines():
        try: 
            dic = json.loads(line)
            if dic['author'] in data.keys():
                if dic['subreddit'] in data[dic['author']].keys():
                    data[dic['author']][dic['subreddit']] +=1
                else:
                    data[dic['author']][dic['subreddit']] =1
            else:
                data[dic['author']] = {}
                data[dic['author']][dic['subreddit']] = 1
        except json.JSONDecodeError:
            continue
    return data

In [15]:
def jsonKeys2int(x):
    if isinstance(x, dict):
            return {int(k):v for k,v in x.items()}
    return x

In [16]:
data = json.load(open('reddit_scrapper/data/scrapped_data4.json','r+'))
subreddit_names_list = json.load(open('reddit_scrapper/data/list_of_unique_subreddits4.json','r+'))
subreddit_index = dict(zip(subreddit_names_list,range(len(subreddit_names_list))))
index_subreddit =  dict(zip(range(len(subreddit_names_list)),subreddit_names_list))

In [17]:
def create_matrix(data,matrix_width,subreddit_index):
    """ Creates matrix filled with zeros and iterates over it filling the cells based on 
        the subreddit-index dictionary"""
    matrix = np.zeros(shape=(len(data),matrix_width))
    for idx,redditor in enumerate(data.values()):
        for key,value in redditor.items():
            matrix[idx,subreddit_index[key]] = value
    return matrix

In [18]:
def update_dictionaries(new_redditors,subreddit_index,index_subreddit,subreddit_names_list):
    """ Updating index-subreddit,subreddit-index dictionaries and subreddit_names_list according to the
        new_redditors- new incoming data"""
    for redditor in new_redditors.values():
        for i in redditor.keys():
            if i not in subreddit_names_list:
                subreddit_index[i] = len(subreddit_index)
                index_subreddit[len(index_subreddit)] = i
                subreddit_names_list.append(i)
    return subreddit_index,index_subreddit,subreddit_names_list

In [19]:
def resize_matrix_width(matrix,subreddit_index):
    """ Updating the width of the main matrix to match it with the incoming data"""
    if matrix.shape[1] != len(subreddit_index):
        extension = np.zeros((matrix.shape[0],len(subreddit_index)-matrix.shape[1]))
        matrix = np.hstack((matrix, extension))
    return matrix 

In [20]:
def update(matrix,new_redditors,subreddit_index,index_subreddit,subreddit_names_list):
    """Function that manages new incoming data and combines it with the main matrix"""
    subreddit_index,index_subreddit,subreddit_names_list = \
    update_dictionaries(new_redditors,subreddit_index,index_subreddit,subreddit_names_list)
    matrix = resize_matrix_width(matrix,subreddit_index)
    recent_data = create_matrix(new_redditors,matrix.shape[1],subreddit_index)
    matrix = np.vstack((matrix, recent_data))
    return matrix,subreddit_index,index_subreddit,subreddit_names_list

### Create matrix

Remove rows and columns where all cells contains integer less or equal to 5. E.g. when a redditor comments less than threshold (6) times in a given reddit we consider an inconsiderable input so we floor it to zero. If a given redditor has commented less than the threshold in all the reddits (0/False vector) we remove him from the data. Same applies to reddit sites.

In [21]:
matrix = create_matrix(data,len(subreddit_names_list),subreddit_index)

In [28]:
mask = np.where(matrix>5,True,False)
rows = ~np.all(mask==False,axis=1)
columns = ~np.all(mask==False,axis=0)
data = matrix[np.ix_(rows,columns)]
df = pd.DataFrame(data,columns=np.squeeze(np.argwhere(columns)))
df.rename(columns=index_subreddit,inplace=True)

In [29]:
df_bool = df.astype(bool).astype(int)

### Clustering

In [24]:
from sklearn.metrics import silhouette_samples, silhouette_score
from sklearn.manifold import TSNE
from sklearn.cluster import DBSCAN
import matplotlib.pyplot as plt
import matplotlib.cm as cm
from itertools import product
import plotly.express as px
from tqdm.notebook import tqdm

In [35]:
data_clustering = df ##Choose boolean data or data with the frequency of posting in a given reddit
upper_limit = 1000 ##  Choose number of most popular reddits
lower_limit = 3 
n_components = 3 ## Choose number of dimensions to project the data onto

In [46]:
most_popular_reddits = data_clustering.sum(axis=0).sort_values(ascending=False)[lower_limit:upper_limit].index
X = data_clustering.loc[:,most_popular_reddits]
X = X.loc[(X.T != 0).any(), (X != 0).any(axis=0)]

In [ ]:
tsne =  TSNE(n_components=n_components,n_jobs=-1,random_state=69)
X_tsne = tsne.fit_transform(X)

In [33]:
clustering = DBSCAN(eps=2.7, min_samples=12,n_jobs=-1).fit(X_tsne)

In [34]:
np.unique(clustering.labels_).shape[0]

348

In [35]:
if n_components == 2:
    X_tsne = pd.DataFrame(X_tsne,columns=['component1','component2'])
    X_tsne['clustering'] = clustering.labels_
    X_tsne['clustering'] = X_tsne['clustering'].astype(str)
    print(f"Number of clusters {pd.unique(X_tsne['clustering']).shape[0]}")
    fig = px.scatter(X_tsne,x="component1", y="component2", color="clustering")
    fig.show()
elif n_components == 3:
    X_tsne = pd.DataFrame(X_tsne,columns=['component1','component2','component3'])
    X_tsne['clustering'] = clustering.labels_
    X_tsne['clustering'] = X_tsne['clustering'].astype(str)
    print(f"Number of clusters {pd.unique(X_tsne['clustering']).shape[0]}")
    fig = px.scatter_3d(X_tsne,x="component1", y="component2",z='component3', color="clustering")
    fig.show()

Number of clusters 348


### Dictionary of subrredits and number of their occurences divided into clusters

In [20]:
clustered_useres_dicts = []

In [21]:
X['clustering'] = clustering.labels_
clustered_users = X.groupby(by=X['clustering']).sum()
clustered_users_matrix = clustered_users.to_numpy().astype(int)
for i in range(clustered_users.to_numpy().shape[0]):
    mask = np.where(clustered_users_matrix[i,:] >0,True,False)
    clustered_useres_dicts.append(dict(zip(clustered_users.columns[mask],clustered_users_matrix[i,:][mask])))

In [22]:
clustered_useres_dicts

[{'neoliberal': 2,
  'dogecoin': 35,
  'nfl': 38,
  'Cringetopia': 44,
  'nextfuckinglevel': 60,
  'funny': 81,
  'pics': 51,
  'conspiracy': 26,
  'leagueoflegends': 42,
  'dankmemes': 41,
  'todayilearned': 51,
  'gaming': 85,
  'aww': 59,
  '196': 17,
  'Eldenring': 53,
  'GME': 16,
  'SquaredCircle': 25,
  'Genshin_Impact': 28,
  'formula1': 47,
  'WhitePeopleTwitter': 49,
  'NoStupidQuestions': 20,
  'movies': 35,
  'IdiotsInCars': 5,
  'DestinyTheGame': 13,
  'NoNewNormal': 20,
  'AskMen': 39,
  'Conservative': 38,
  'Cricket': 8,
  'Games': 35,
  'facepalm': 37,
  'baseball': 49,
  'apexlegends': 17,
  'PoliticalHumor': 10,
  'pcmasterrace': 54,
  'europe': 29,
  'MMA': 10,
  'Gamingcirclejerk': 6,
  'HolUp': 8,
  'CFB': 4,
  'de': 9,
  'mildlyinteresting': 23,
  'FortNiteBR': 33,
  'Unexpected': 24,
  'anime': 15,
  'PS5': 15,
  'Bitcoin': 9,
  'nottheonion': 39,
  'SafeMoon': 17,
  'Minecraft': 34,
  'Whatcouldgowrong': 16,
  'onlyfansgirls101': 3,
  'MadeMeSmile': 14,
  'Show

### Plot silhouette measure

In [23]:
def plot_silhouette(X,cluster_labels,n_clusters,silhouette_avg,sample_silhouette_values):
    fig, ax1 = plt.subplots(1, 1)
    fig.set_size_inches(18, 7)
    ax1.set_xlim([-0.1, 1])
    y_lower = 10
    for i in range(n_clusters):
        ith_cluster_silhouette_values = \
            sample_silhouette_values[cluster_labels == i]

        ith_cluster_silhouette_values.sort()

        size_cluster_i = ith_cluster_silhouette_values.shape[0]
        y_upper = y_lower + size_cluster_i

        color = cm.nipy_spectral(float(i) / n_clusters)
        ax1.fill_betweenx(np.arange(y_lower, y_upper),
                          0, ith_cluster_silhouette_values,
                          facecolor=color, edgecolor=color, alpha=0.7)
        y_lower = y_upper + 10  # 10 for the 0 samples

    ax1.set_title("The silhouette plot for the various clusters.")
    ax1.set_xlabel("The silhouette coefficient values")
    ax1.set_ylabel("Cluster label")

    ax1.axvline(x=silhouette_avg, color="red", linestyle="--")

    ax1.set_yticks([])  # Clear the yaxis labels / ticks
    ax1.set_xticks([-0.1, 0, 0.2, 0.4, 0.6, 0.8, 1])
    plt.suptitle(("Silhouette analysis for DBSCAN clustering on sample data "
                  "with n_clusters = %d" % n_clusters),
                 fontsize=14, fontweight='bold')
    plt.show()

### Find the best parameters

In [24]:
show_plot = False
eps_list = list(np.around(np.arange(2, 5.0, 0.1),2))
lower_min_samples = 3
higher_min_samples = 15
min_samples_list = list(np.arange(lower_min_samples, higher_min_samples, 1))
pairs = list(product(eps_list,min_samples_list))
n = 2 # early skip
results = []
last_n_scores = []
progress_bar_value = 0
with tqdm(total=100, desc="Percentage done") as pbar:  
    for i in range(len(pairs)):
        if i == len(pairs):
            break
        eps,min_samples = pairs[i]
        cluster_labels = DBSCAN(eps=eps, min_samples=min_samples,n_jobs=-1).fit_predict(X_tsne)
        silhouette_avg = silhouette_score(X_tsne, cluster_labels)
        results.append((np.unique(cluster_labels).shape[0],eps,min_samples,silhouette_avg))
        last_n_scores.append(silhouette_avg)
        if  np.unique(last_n_scores[-n:]).shape[0] ==1 and len(last_n_scores)>n:
            last_n_scores = []
            if i < len(pairs):
                skip = higher_min_samples-int(pairs[i][1])
                if len(pairs)-skip+1 > 2*len(min_samples_list):
                    pairs = pairs[skip-1:]
        pbar.update((i/len(pairs) - progress_bar_value)*100)
        progress_bar_value = i/len(pairs)
        if show_plot:
            plot_silhouette(X_tsne,cluster_labels,np.unique(cluster_labels).shape[0],silhouette_avg,sample_silhouette_values)
    pbar.update(100-progress_bar_value)


In [25]:
results = pd.DataFrame(results,columns=['n_clusters','eps','min_samples','silhouette'])
results = results.sort_values(by='silhouette',ascending=False)
results.head(10)

n_clusters  eps  min_samples  silhouette
0          899  2.0            3    0.292589
12         850  2.1            3    0.287306
2          718  2.0            5    0.284513
1          777  2.0            4    0.283082
13         737  2.1            4    0.276700
3          678  2.0            6    0.275266
14         682  2.1            5    0.273058
15         649  2.1            6    0.270871
24         812  2.2            3    0.266613
25         710  2.2            4    0.263338

In [36]:
results.drop_duplicates(subset=['n_clusters'],keep='first').plot.line(x='n_clusters',y='silhouette',figsize=(16,10))

<AxesSubplot:xlabel='n_clusters'>

### PCA test

In [48]:
from sklearn.decomposition import PCA

In [49]:
pca = PCA().fit(X)
x = np.cumsum(pca.explained_variance_ratio_)
fig = px.line( y=x, x=list(range(len(x))))
fig.update_layout(title='PCA algorithm',
                   xaxis_title='number of components',
                   yaxis_title='cumulative explained variance')
fig.show()

# Ball Tree

In [51]:
from sklearn.neighbors import BallTree

In [179]:
tree = BallTree(X)

In [200]:
n = 2 # index of initial user
user_vector = np.expand_dims(X.loc[n].to_numpy(),0)
dist, ind = tree.query(user_vector,k=100)

Initial user

In [201]:
mask = np.where(user_vector>0,True,False)[0]
users_subrredits = X.loc[n].index[mask]
query_user = dict(zip(X.loc[n].index[mask],user_vector[0][mask]))
query_user

{'amcstock': 55.0, 'AMCSTOCKS': 20.0}

Found users

In [204]:
nearest_nb_dict = []
nearest_nb = X.iloc[list(*ind)[1:]]
nearest_nb_np = nearest_nb.to_numpy().astype(int)
for i in range(nearest_nb_np.shape[0]):
    mask = np.where(nearest_nb_np[i,:] >0,True,False)
    nearest_nb_dict.append(dict(zip(nearest_nb.columns[mask],nearest_nb_np[i,:][mask])))

Recommendation by number of comments

In [205]:
neighbors = nearest_nb.sum(axis=0)
columns = set(neighbors.index)- set(users_subrredits)
neighbors = neighbors.loc[columns]

In [206]:
neighbors[neighbors >0].sort_values(ascending=False)

WallStreetbetsELITE      192.0
GME                       75.0
dogecoin                  60.0
CryptoCurrency            27.0
Wallstreetbetsnew         24.0
                         ...  
PersonalFinanceCanada      1.0
Spielstopp                 1.0
iamatotalpieceofshit       1.0
Tinder                     1.0
MarvelStudiosSpoilers      1.0
Length: 143, dtype: float64

Recommendation by number of users

In [207]:
neighbors = nearest_nb.astype(bool).astype(int).sum(axis=0)
columns = set(neighbors.index)- set(users_subrredits)
neighbors = neighbors.loc[columns]

In [209]:
neighbors[neighbors >0].sort_values(ascending=False)

WallStreetbetsELITE      31
GME                      15
dogecoin                 11
Wallstreetbetsnew         9
CryptoCurrency            8
                         ..
IdiotsInCars              1
DestinyTheGame            1
WinStupidPrizes           1
videos                    1
MarvelStudiosSpoilers     1
Length: 143, dtype: int64

In [34]:
show_plot = False
eps_list = list(np.around(np.arange(3, 6.0, 0.1),2))
lower_min_samples = 8
higher_min_samples = 17
min_samples_list = list(np.arange(lower_min_samples, higher_min_samples, 1))
pairs = list(product(eps_list,min_samples_list))
n = 2 # early skip
results = []
last_n_scores = []
progress_bar_value = 0
with tqdm(total=100, desc="Percentage done") as pbar:  
    for i in range(len(pairs)):
        if i == len(pairs):
            break
        eps,min_samples = pairs[i]
        cluster_labels = DBSCAN(eps=eps, min_samples=min_samples,n_jobs=-1).fit_predict(X_tsne)
        silhouette_avg = silhouette_score(X_tsne, cluster_labels)
        results.append((np.unique(cluster_labels).shape[0],eps,min_samples,silhouette_avg))
        last_n_scores.append(silhouette_avg)
        if  np.unique(last_n_scores[-n:]).shape[0] ==1 and len(last_n_scores)>n:
            last_n_scores = []
            if i < len(pairs):
                skip = higher_min_samples-int(pairs[i][1])
                if len(pairs)-skip+1 > 2*len(min_samples_list):
                    pairs = pairs[skip-1:]
        pbar.update((i/len(pairs) - progress_bar_value)*100)
        progress_bar_value = i/len(pairs)
        if show_plot:
            plot_silhouette(X_tsne,cluster_labels,np.unique(cluster_labels).shape[0],silhouette_avg,sample_silhouette_values)
    pbar.update(100-progress_bar_value)


KeyboardInterrupt: 

In [29]:
results = pd.DataFrame(results,columns=['n_clusters','eps','min_samples','silhouette'])
results = results.sort_values(by='silhouette',ascending=False)
results.head(10)

n_clusters  eps  min_samples  silhouette
2          26  2.0           10   -0.203117
1          28  2.0            9   -0.213223
0          38  2.0            8   -0.214894

In [ ]:
from mlxtend.preprocessing import TransactionEncoder
from mlxtend.frequent_patterns import apriori
from mlxtend.frequent_patterns import association_rules

In [ ]:
frequent_itemsets = apriori(df_bool, min_support=0.01, use_colnames=True)
rules = association_rules(frequent_itemsets, 
                  metric='confidence', 
                  min_threshold=0.7)

In [ ]:
rules.to_json("data/arules.json")